In [1]:
import ee
ee.Authenticate()
ee.Initialize()

Enter verification code: 4/1AbUR2VOjhqjyDQLSqzYueN2MTyifx9lRZQfhfWmcXTGcRxH-Ktg48tEU2y0

Successfully saved authorization token.


In [2]:
import geemap

In [15]:
def getS1Image(startDate, endDate, roi, polarisation):
    '''
    Returns a collection of Sentinel 1 images
    Parameters:
    startDate (str):starting date of the collection
    endDate (str):end date of the collection
    roi (ee Geometry): region of interest to filter
    polarization (str): SAR polarisation VV, HH    
      
    Returns:
    filtred ee image collection (ee.imagecollection):Collection of Sentinel 1 images 
    '''
    S1_collection = (
        ee.ImageCollection('COPERNICUS/S1_GRD')
        .filterBounds(roi)
        .filterDate(startDate,endDate)
        .filter(ee.Filter.eq('instrumentMode', 'IW'))
        .filter(ee.Filter.eq("orbitProperties_pass", "DESCENDING")) 
        .select(polarisation))
    return S1_collection

In [20]:
roi = ee.Geometry.Point([-0.627983, 52.074361]).buffer(1000)

SAR_images = getS1Image(startDate= '2023-01-01', 
                        endDate='2023-05-15',
                        roi = roi,
                        polarisation= "VV" )
# get info
SAR_images

In [98]:
Map3 = geemap.Map()
Map3.center_object(roi)
Map3.add_basemap("HYBRID")
Map3.addLayer(SAR_images.first(),{'min': -25, 'max': 0},name="SAR")
#Map3

In [28]:
def getLandsatImages(roi, startDate, endDate, min_cloud_cover):
    '''gets images from LANDSAT and has a minimum cloud cover entry '''
    
    L8_collection = (ee.ImageCollection('LANDSAT/LC08/C02/T1_L2')
    .filterDate(startDate, endDate)
    .filterBounds(roi)
    .filter(ee.Filter.lt('CLOUD_COVER', min_cloud_cover)))
    return L8_collection
    
    

In [31]:
roi = ee.Geometry.Point([-0.627983, 52.074361]).buffer(1000)

L8_collection = getLandsatImages(roi, '2023-01-01', '2023-05-05', 90)
L8_collection

In [113]:
Map4 = geemap.Map()
Map4.center_object(roi)
Map4.addLayer(L8_collection.first().multiply(0.0000275).add(-0.2),{'min': 0, 'max': 0.3}, name = 'first')
Map4

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

Apply a function for sentinel over an image collection

In [38]:
roi = ee.Geometry.Point([-0.627983, 52.074361]).buffer(1000)
# Chain multiple filters  
s2_collection = (ee.ImageCollection('COPERNICUS/S2_HARMONIZED')
    .filterDate('2022-05-01', '2023-05-01')
    .filterBounds(roi)
    .filter(ee.Filter.lt('CLOUDY_PIXEL_PERCENTAGE', 20)))

# image composite using a median reducer
S2_median = s2_collection.median()

In [37]:
def getNDVI(image):
    ''' calculates NDVI and adds it to the image as a new band '''
    ndvi = image.normalizedDifference(['B8', 'B4']).rename('NDVI')
    addNdvi = image.addBands(ndvi)
    return addNdvi

In [39]:
S2_NDVI = getNDVI(S2_median)
S2_NDVI

In [40]:
ndviParams = {'bands': ['NDVI'],
              'palette': ['red', 'orange', 'yellow', 'green'], 
              'min': -1,
              'max': 1}

In [101]:
Map5 = geemap.Map()
Map5.center_object(roi)
Map5.addLayer(S2_NDVI,vis_params=ndviParams,name="NDVI") # now need to add ndvi as a band
Map5.addLayerControl()

In [43]:
# to use getNDVI() over the entire collection we need to use the argument .map()
addNDVIS2_coll = s2_collection.map(getNDVI) 
addNDVIS2_coll

In [102]:
Map5.addLayer(addNDVIS2_coll.first(),vis_params=ndviParams,name="NDVI_first")
#Map5

# Exercise

In [78]:
def maskL8sr(image):
    # Get the pixel QA band.
    qa = image.select('QA_PIXEL')
    # Bits 3 and 4 are cloud shadow and cloud, respectively
    cloudShadowBitMask = int(2**4)
    cloudsBitMask = int(2**3)
    # Both flags should be set to zero, indicating clear conditions.
    mask = qa.bitwiseAnd(cloudShadowBitMask).eq(0).And(qa.bitwiseAnd(cloudsBitMask).eq(0))
    masked = image.updateMask(mask)
    return masked

def getLandsat(roi, startDate, endDate, min_cloud_cover):
    '''gets images from LANDSAT and has a minimum cloud cover entry '''
    
    L8_collection = (ee.ImageCollection('LANDSAT/LC08/C02/T1_L2')
    .filterDate(startDate, endDate)
    .filterBounds(roi)
    .filter(ee.Filter.lt('CLOUD_COVER', min_cloud_cover)))
    return L8_collection


def getLSNDVI(image):
    ''' calculates NDVI and adds it to the image as a new band for LandSat '''
    ndvi = image.normalizedDifference(['SR_B5', 'SR_B4']).rename('NDVI')
    addNdvi = image.addBands(ndvi)
    return addNdvi

Apply the provided cloud function mapping to the Landsat SR collection in order to mask out cloudy areas.


Apply the NDVI (Normalized Difference Vegetation Index) function to the collection

In [103]:
roi = ee.Geometry.Point([-0.627983, 52.074361]).buffer(1000)

ls_collection = getLandsatImages(roi, '2017-05-01', '2023-05-01', 40)

In [104]:
cloud_masked_col = ls_collection.map(maskL8sr)
cloud_masked_col

In [85]:
first_image = cloud_masked_col.first().multiply(0.0000275).add(-0.2)
first_image

In [88]:
rgbParams = {'bands': ['SR_B2', 'SR_B3', 'SR_B4'], 
              'min': 0,
              'max': 0.3}

In [111]:
Map = geemap.Map()
Map.center_object(roi)
Map.addLayer(first_image,vis_params=rgbParams, name = 'cloud pixels removed')
Map.addLayerControl()
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

## Calculate NDVI

In [109]:
cloud_masked_col_with_ndvi = cloud_masked_col.map(getLSNDVI)
cloud_masked_col_with_ndvi_sorted = cloud_masked_col_with_ndvi.sort('CLOUD_COVER', opt_ascending=True)
cloud_masked_col_with_ndvi

In [110]:
first_image_with_ndvi = cloud_masked_col_with_ndvi.first()
Map = geemap.Map()
Map.center_object(roi)
Map.addLayer(first_image_with_ndvi,vis_params=ndviParams, name = 'ndvi')
Map.addLayerControl()
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

TraitError: The 'east' trait of a Map instance expected a float, not the NoneType None.

TraitError: The 'east' trait of a Map instance expected a float, not the NoneType None.

TraitError: The 'east' trait of a Map instance expected a float, not the NoneType None.

TraitError: The 'east' trait of a Map instance expected a float, not the NoneType None.